# 第2組 第四次讀書會：社群網路分析

**資料抓取區間** : 2022/5/18~2023/5/18

本週課程利用之前使用的PTT美食版，抓取近一年有關高雄之美食，並排除素食類及速食類（麥當勞、肯德基），觀察發文者與回文者的情況

In [1]:
! pip install pyvis networkx pandas numpy


[notice] A new release of pip is available: 23.0.1 -> 23.1.2
[notice] To update, run: pip install --upgrade pip


In [2]:
import pandas as pd
import numpy as np
import pyvis
import networkx as nx
import IPython

In [7]:
raw_data = pd.read_csv('sna2023s_food.csv')
raw_data = raw_data[raw_data.artComment != '[]']
# raw_data = raw_data.sample(round(raw_data.shape[0]/4))
# print(raw_data.shape)
raw_data.head()


system_id                                             artUrl  \
3           4  https://www.ptt.cc/bbs/Food/M.1652974809.A.3C2...   
9          10  https://www.ptt.cc/bbs/Food/M.1653287940.A.C33...   
11         12  https://www.ptt.cc/bbs/Food/M.1653357000.A.104...   
12         13  https://www.ptt.cc/bbs/Food/M.1653375569.A.39C...   
19         20  https://www.ptt.cc/bbs/Food/M.1653553234.A.AE0...   

                  artTitle              artDate   artPoster artCatagory  \
3    [徵人]5/2017:30NIBBON一位  2022-05-19 23:40:06  birdhackor        Food   
9   [食記]高雄前金｜外帶一隻貓MIAOTOGO  2022-05-23 14:38:57   syuanfeng        Food   
11       [食記]台南三井薄多義義式手工披薩  2022-05-24 09:49:55     designW        Food   
12          [食記]三民區麵食-尋米拌麵  2022-05-24 14:59:27   BOSOMGIRL        Food   
19        [食記]高雄鹽埕｜一等一咖啡茶飲  2022-05-26 16:20:31   syuanfeng        Food   

                                           artContent  \
3   我原本訂了兩個人的位子要跟朋友一起吃\n\n但朋友今天身體不舒服，若明日沒有改善，「有可能」...   
9   餐廳名稱：外帶一隻貓MIAO TO GO\n   消費時間：2022年5月\n   地址：8...   
11  餐廳名稱：台南。薄多義義式手工披薩(台南三井OUTLET店)\n   消費時間：2022年/...   
12  餐廳名稱：尋米拌麵\n消費時間：2021年/12月\n\n營業：10:30-14:30 / ...   
19  餐廳名稱：一等一咖啡茶飲\n   消費時間：2022年5月\n   地址：803高雄市鹽埕區...   

                                           artComment            e_ip  \
3   [{"cmtStatus": "→", "cmtPoster": "ginsengwolf"...   111.243.44.51   
9   [{"cmtStatus": "推", "cmtPoster": "Miniscus", "...  124.218.69.179   
11  [{"cmtStatus": "→", "cmtPoster": "linuscool98"...    210.60.92.15   
12  [{"cmtStatus": "推", "cmtPoster": "Larry0113ooo...  218.166.238.43   
19  [{"cmtStatus": "推", "cmtPoster": "Rosineivy", ...  124.218.69.179   

           insertedDate dataSource  
3   2022-05-20 01:11:59        ptt  
9   2022-05-24 01:12:12        ptt  
11  2022-05-25 01:12:14        ptt  
12  2022-05-25 01:12:14        ptt  
19  2022-05-27 01:12:24        ptt

In [8]:
#parse comment

def getComtInfo(com):
  cmters,cmt_statuss = [],[]
  com = eval(com)
  for i in com:
    print(i)
    cmters.append(i['cmtPoster'])
    cmt_statuss.append(i['cmtStatus'])
  return pd.Series([cmters, cmt_statuss])

raw_data[['artComter','artStatus']] = raw_data['artComment'].apply(lambda r: getComtInfo(r))

{'cmtStatus': '→', 'cmtPoster': 'ginsengwolf', 'cmtContent': ':噓在哪，可以噓嗎', 'cmtDate': '2022-05-20 01:05:00'}
{'cmtStatus': '→', 'cmtPoster': 'mouse07', 'cmtContent': ':真的有這麼想吃？', 'cmtDate': '2022-05-20 01:27:00'}
{'cmtStatus': '→', 'cmtPoster': 'iPhone3GS', 'cmtContent': ':好慘', 'cmtDate': '2022-05-20 12:01:00'}
{'cmtStatus': '→', 'cmtPoster': 'saku0317', 'cmtContent': ':候補到沒尊嚴', 'cmtDate': '2022-05-21 10:41:00'}
{'cmtStatus': '推', 'cmtPoster': 'Miniscus', 'cmtContent': ':菜單裝潢都好棒，有機會要去看看!', 'cmtDate': '2022-05-23 15:04:00'}
{'cmtStatus': '→', 'cmtPoster': 'linuscool98', 'cmtContent': ':薄多義不錯吃不過這幾天也漲價了', 'cmtDate': '2022-05-24 16:20:00'}
{'cmtStatus': '→', 'cmtPoster': 'linuscool98', 'cmtContent': ':更正這幾年', 'cmtDate': '2022-05-24 16:20:00'}
{'cmtStatus': '推', 'cmtPoster': 'Larry0113ooo', 'cmtContent': ':Cp值不賴', 'cmtDate': '2022-05-24 16:56:00'}
{'cmtStatus': '推', 'cmtPoster': 'Rosineivy', 'cmtContent': ':推一等一的悠閒居家感~', 'cmtDate': '2022-05-26 19:47:00'}
{'cmtStatus': '推', 'cmtPoster': 'sfot

In [9]:
raw_data = raw_data.explode(['artComter','artStatus'])
socail_data = raw_data[['artUrl','artPoster','artComter','artStatus']]
socail_data.head(10)


artUrl   artPoster  \
3   https://www.ptt.cc/bbs/Food/M.1652974809.A.3C2...  birdhackor   
3   https://www.ptt.cc/bbs/Food/M.1652974809.A.3C2...  birdhackor   
3   https://www.ptt.cc/bbs/Food/M.1652974809.A.3C2...  birdhackor   
3   https://www.ptt.cc/bbs/Food/M.1652974809.A.3C2...  birdhackor   
9   https://www.ptt.cc/bbs/Food/M.1653287940.A.C33...   syuanfeng   
11  https://www.ptt.cc/bbs/Food/M.1653357000.A.104...     designW   
11  https://www.ptt.cc/bbs/Food/M.1653357000.A.104...     designW   
12  https://www.ptt.cc/bbs/Food/M.1653375569.A.39C...   BOSOMGIRL   
19  https://www.ptt.cc/bbs/Food/M.1653553234.A.AE0...   syuanfeng   
19  https://www.ptt.cc/bbs/Food/M.1653553234.A.AE0...   syuanfeng   

       artComter artStatus  
3    ginsengwolf         →  
3        mouse07         →  
3      iPhone3GS         →  
3       saku0317         →  
9       Miniscus         推  
11   linuscool98         →  
11   linuscool98         →  
12  Larry0113ooo         推  
19     Rosineivy         推  
19         sfoto         推

In [10]:
socail_data.artStatus.unique()

array(['→', '推', '噓'], dtype=object)

簡單劃出文章、發文者、評論者的網路

In [11]:
# 建立邊的資料
import random


po_df = socail_data[['artPoster','artUrl']].drop_duplicates().rename(columns = {'artPoster':'src','artUrl':'dis'})
sample_url = random.choices(po_df.dis.unique().tolist(),k=300)
po_df = po_df[po_df.dis.isin(sample_url)]
re_df = socail_data[['artComter','artUrl','artStatus']].rename(columns = {'artComter':'src','artUrl':'dis','artStatus':'weight'})
re_df = re_df[re_df.dis.isin(sample_url)]
re_df = re_df[~re_df['src'].isna()]



def convertStatus(s):
  if s == '推':
    return 2
  elif s == '→':
    return 1
  else :
    return -1
re_df['weight'] = re_df['weight'].map(convertStatus)
re_df = re_df.groupby(['src','dis']).sum().reset_index()

# 設定分數低的為紅色
def getColor(w):
  if w>0:
    return 'green'
  else:
    return 'red'
re_df['color'] = re_df.weight.map(getColor)



In [12]:
re_df

src                                                dis  weight  \
0    ARCHER2234  https://www.ptt.cc/bbs/Food/M.1665842006.A.4CD...       4   
1         ASEVE  https://www.ptt.cc/bbs/Food/M.1681403381.A.012...       2   
2        AlphaD  https://www.ptt.cc/bbs/Food/M.1659099975.A.1E1...       1   
3        AlphaD  https://www.ptt.cc/bbs/Food/M.1662194112.A.497...       1   
4        AlphaD  https://www.ptt.cc/bbs/Food/M.1662553871.A.27E...       2   
..          ...                                                ...     ...   
374    zhengzhe  https://www.ptt.cc/bbs/Food/M.1661837378.A.98D...       1   
375     zyc5566  https://www.ptt.cc/bbs/Food/M.1655268051.A.324...       1   
376     zyc5566  https://www.ptt.cc/bbs/Food/M.1655270847.A.09F...       2   
377        zzro  https://www.ptt.cc/bbs/Food/M.1681403381.A.012...      -1   
378    zzz50126  https://www.ptt.cc/bbs/Food/M.1655268051.A.324...       2   

     color  
0    green  
1    green  
2    green  
3    green  
4    green  
..     ...  
374  green  
375  green  
376  green  
377    red  
378  green  

[379 rows x 4 columns]

In [13]:
# 人為綠色節點
# po文為橘色節點

netWork = pyvis.network.Network(notebook=True, cdn_resources='in_line',directed=True)
person = list(set(po_df.src.unique().tolist()+re_df.src.unique().tolist()))
url = po_df.dis.unique().tolist()
netWork.add_nodes(
    nodes = person,
    value = [1 for i in range(len(person))],
    color = ['#66CDAA' for i in range(len(person))],
    title = person
)
netWork.add_nodes(
    nodes = url,
    value = [2 for i in range(len(url))],
    color = ['#FFB366' for i in range(len(url))],
    title = url
)
for i in po_df.to_numpy():
  netWork.add_edge(i[0],i[1],width = 2,color='grey')
for i in re_df.to_numpy():
  netWork.add_edge(i[0],i[1],width = 2,color=i[3])

# 設定layout
netWork.repulsion()

# netWork.toggle_physics(True)
# netWork.set_options("""
# const options = {
#   "physics": {
#     "forceAtlas2Based": {
#       "springLength": 100
#     },
#     "minVelocity": 0.75,
#     "solver": "forceAtlas2Based",
#     "timestep": 0.48
#   }
# }
# """)

netWork.show("./basic_netWork.html")
IPython.display.HTML('basic_netWork.html')

./basic_netWork.html


*1綠色為推的回覆,紅色是噓，大概是兩大群（回覆較多），以及其他小群*

https://www.ptt.cc/bbs/Food/M.1681403381.A.012.html：
高雄3億流水席超狂菜色"鮪魚現殺秀"上桌 標題下人引起討論（獨立的那個大圓）

https://www.ptt.cc/bbs/Food/M.1661837378.A.98D.html：
【2022 米其林一星餐廳】



計算網友之間的關係

In [ ]:
pos_cmt = socail_data.copy()
pos_cmt = pos_cmt[~pos_cmt.artComter.isna()]
pos_cmt.head(10)

artUrl   artPoster  \
3   https://www.ptt.cc/bbs/Food/M.1652974809.A.3C2...  birdhackor   
3   https://www.ptt.cc/bbs/Food/M.1652974809.A.3C2...  birdhackor   
3   https://www.ptt.cc/bbs/Food/M.1652974809.A.3C2...  birdhackor   
3   https://www.ptt.cc/bbs/Food/M.1652974809.A.3C2...  birdhackor   
9   https://www.ptt.cc/bbs/Food/M.1653287940.A.C33...   syuanfeng   
11  https://www.ptt.cc/bbs/Food/M.1653357000.A.104...     designW   
11  https://www.ptt.cc/bbs/Food/M.1653357000.A.104...     designW   
12  https://www.ptt.cc/bbs/Food/M.1653375569.A.39C...   BOSOMGIRL   
19  https://www.ptt.cc/bbs/Food/M.1653553234.A.AE0...   syuanfeng   
19  https://www.ptt.cc/bbs/Food/M.1653553234.A.AE0...   syuanfeng   

       artComter artStatus  
3    ginsengwolf         →  
3        mouse07         →  
3      iPhone3GS         →  
3       saku0317         →  
9       Miniscus         推  
11   linuscool98         →  
11   linuscool98         →  
12  Larry0113ooo         推  
19     Rosineivy         推  
19         sfoto         推

In [ ]:
pos_cmt['score'] = pos_cmt['artStatus'].apply(lambda r: convertStatus(r))
pos_cmt = pos_cmt.groupby(['artComter','artPoster']).sum('score').reset_index()
pos_cmt = pos_cmt[pos_cmt.score>=0]
pos_cmt = pos_cmt[pos_cmt.artComter != pos_cmt.artPoster]
# pos_cmt.score = 1
pos_cmt

artComter   artPoster  score
0    ARCHER2234    a0079527      4
1         ASEVE  KenHiraiTW      2
3     Alphaplus     reesion      0
4    Andriy6016      anan00      3
6        Arutha     vhygdih      2
..          ...         ...    ...
397  zeroyaking     reesion      2
398    zhengzhe  mark126688      1
399     zyc5566     reesion      1
400     zyc5566   syuanfeng      2
402    zzz50126     reesion      2

[385 rows x 3 columns]

In [ ]:
pers = np.unique(pos_cmt[['artComter', 'artPoster']])
mat = pd.pivot_table(pos_cmt,index = 'artComter', columns = 'artPoster' ,values='score' ).fillna(0)\
  .reindex(columns=pers, index=pers, fill_value=0).to_numpy()
print(mat.shape)
tri = (np.tril(mat,-1).T + np.triu(mat,1))
mat_s = tri+tri.T

# # print((mat == mat.transpose()).all())

# G = nx.DiGraph(mat)
# G_sub = sorted(nx.connected_components(G), key=len, reverse=True)
# G_max_sub = G.subgraph(G_sub[0])
# # 重新定義 mat
# mat = nx.adjacency_matrix(G_max_sub).todense()
# node_idx = list(G_max_sub.nodes)
# # mat = mat[np.ix_(node_idx,node_idx)]
# pers = pers[node_idx]
# print((mat == mat.transpose()).all())

# # 計算無向圖的adj


(377, 377)


In [ ]:
def random_color():
  r = lambda: random.randint(0,255)
  return '#%02X%02X%02X' % (r(),r(),r())

def matPresentGraph(mat:np.array,node_id:list,node_type:list=None,node_value:list = None,directed = True,edge_color=None) -> pyvis.network.Network:

  if directed != True:
    if (mat == mat.transpose()).all():
      print('matrix is Symmetric')
    else:
      print('matrix is not Symmetric')
  if node_type == None:
    c = random_color()
    node_colors = [c for i in range(len(node_id))]
    node_type = [" " for i in range(len(node_id))]
  else:
    node_color_map = {}
    for i in set(node_type):
      while True:
        c = random_color()
        if c not in node_color_map.values():
          break
      node_color_map[i] = c
    node_colors = [node_color_map[i] for i in node_type]
  # print(node_colors)
  if edge_color == None:
    edge_color = random_color()
  edge_color = random_color()
  if node_value == None:
    node_value = [1 for i in range(len(node_id))]

  net = pyvis.network.Network(notebook=True, directed = directed, cdn_resources='in_line')
  
  titles_list = []
  for i ,j in zip(node_id,node_type):
    titles_list.append(str(i)+":"+str(j))

  net.add_nodes(
      nodes = node_id,
      value = node_value,
      label = node_id,
      title = titles_list,
      color = node_colors
  )

  for row in range(len(node_id)):
    for col in range(len(node_id)):
      if mat[row][col]>0.:
        net.add_edge(
            node_id[row],node_id[col],width = mat[row][col],color = edge_color,title = mat[row][col]
        )
  net.repulsion()
  return net


In [ ]:
# 定義發文者（po）、評論者(cmt)、兩者兼具(both)
node_type = []

cmt_list = pos_cmt['artComter'].unique().tolist()
po_list = pos_cmt['artPoster'].unique().tolist()
both_list = list(set(cmt_list) & set(po_list))
for p in pers:
  if p in both_list:
    node_type.append('both')

  elif p in cmt_list:
    node_type.append('cmt')

  elif p in po_list:
    node_type.append('po')



In [ ]:
net = matPresentGraph(mat = mat,node_id = pers,node_type = node_type)
net.show("./pers_netWork.html")
IPython.display.HTML('pers_netWork.html')

./pers_netWork.html


2從此圖看出有多位使用者對不同文章進行發言
粉色為po文，藍色為評論者，紫色為有評論及有po文者。
syuanfeng為紫色的，意味其會發文，並會針對熱門議題進行回覆提供意見。
KenHiraiTW就是發三億流水席文章的貼文者。

計算eigenvector centrality （無向圖） 算出這個人的重要程度

In [ ]:

eigenvec = np.array(list(nx.eigenvector_centrality(nx.Graph(mat_s),max_iter = 10000).values()))
eigenvec = (eigenvec-np.min(eigenvec))/(np.max(eigenvec)-np.min(eigenvec))


In [ ]:
q = np.quantile(eigenvec,[.2,.4,.6,.8])
q

array([1.31802321e-05, 8.52445354e-05, 3.55782481e-04, 3.95398310e-03])

In [ ]:
node_value = []


for i in eigenvec:

  if i > q[3]: 
    node_value.append(25)
  elif i >q[2]:
    node_value.append(20)
  elif i>q[1]:
    node_value.append(15)
  elif i>q[0]:
    node_value.append(10)
  else:
    node_value.append(5)
net = matPresentGraph(mat = mat,node_id = pers,node_type = node_type,node_value = node_value,directed=False)
net.show("./pers_eig_netWork.html")
IPython.display.HTML('pers_eig_netWork.html')


matrix is not Symmetric
./pers_eig_netWork.html


3我們可以發現有多次評論的人，或是評論的文章同時有多人評論的，重要程度愈高（節點越大）
有較多關係（連線）的會集中於中間
和上面那張圖所找的關聯相同，但可看出分離的那個比較不重要，而下面的圓和其他的叫相關，意味更重要，故節點較大。

PageRank (有向圖)

In [ ]:
# Digraph 設定有向圖
pagerank = np.array(list(nx.pagerank(nx.DiGraph(mat)).values()))
# pagerank = (pagerank-np.min(pagerank))/(np.max(pagerank)-np.min(pagerank))
pagerank

array([0.00149109, 0.00149109, 0.02854508, 0.00149109, 0.00149109,
       0.00149109, 0.01888394, 0.00149109, 0.00149109, 0.00149109,
       0.00149109, 0.00149109, 0.00149109, 0.00149109, 0.00149109,
       0.00149109, 0.00149109, 0.00149109, 0.00149109, 0.00149109,
       0.00149109, 0.00149109, 0.00149109, 0.00942025, 0.00149109,
       0.00149109, 0.00275893, 0.00149109, 0.00149109, 0.00149109,
       0.00149109, 0.00149109, 0.00548739, 0.00149109, 0.00149109,
       0.0522048 , 0.0135356 , 0.00149109, 0.00149109, 0.00149109,
       0.00282747, 0.00149109, 0.00149109, 0.00149109, 0.00149109,
       0.00149109, 0.00149109, 0.00149109, 0.00149109, 0.00149109,
       0.00149109, 0.00275893, 0.00149109, 0.00149109, 0.00149109,
       0.00149109, 0.00149109, 0.00149109, 0.00149109, 0.00149109,
       0.00149109, 0.00149109, 0.00149109, 0.00149109, 0.00149109,
       0.00149109, 0.00149109, 0.00149109, 0.00402678, 0.00149109,
       0.00149109, 0.00149109, 0.00149109, 0.00275893, 0.00149

In [ ]:
net = matPresentGraph(mat = mat,node_id = pers,node_type = node_type,node_value=(pagerank*1000).tolist())
net.show("./pers_page_netWork.html")
IPython.display.HTML('pers_page_netWork.html')


./pers_page_netWork.html


4可以看出indegree 較多，重要程度愈高，只有po文的人節點較大，回覆的人節點不會太大。

Hits score （有向圖）分為in/out

In [ ]:
out_,in_ = nx.hits(nx.DiGraph(mat),max_iter=100)
out_,in_ = np.array(list(out_.values())),np.array(list(in_.values()))
out_ = (out_-np.min(out_))/(np.max(out_)-np.min(out_))
in_ = (in_-np.min(in_))/(np.max(in_)-np.min(in_))


In [ ]:
in_q = np.quantile(in_,[.2,.4,.6,.8])
out_q = np.quantile(out_,[.2,.4,.6,.8])


In [ ]:
in_q

array([1.29303696e-16, 1.38485887e-16, 1.48201429e-16, 1.64816000e-16])

In [ ]:
node_value = []


for i in out_:
  if i > out_q[3]:
    node_value.append(25)
  elif i >out_q[2]:
    node_value.append(20)
  elif i>out_q[1]:
    node_value.append(15)
  elif i>out_q[0]:
    node_value.append(10)
  else:
    node_value.append(5)

net = matPresentGraph(mat = mat,node_id = pers,node_type = node_type,node_value=node_value)
net.show("./pers_out_netWork.html")
IPython.display.HTML('pers_out_netWork.html')

./pers_out_netWork.html


5pers_out_netWork

In [ ]:
node_value = []
for i in in_:
  if i > in_q[3]:
    node_value.append(25)
  elif i >in_q[2]:
    node_value.append(20)
  elif i>in_q[1]:
    node_value.append(15)
  elif i>in_q[0]:
    node_value.append(10)
  else:
    node_value.append(5)

net = matPresentGraph(mat = mat,node_id = pers,node_type = node_type,node_value=node_value)
net.show("./pers_in_netWork.html")
IPython.display.HTML('pers_in_netWork.html')

./pers_in_netWork.html


6可以發現indegree/outdegree的多寡會決定其重要程度

betweenness centrality

In [ ]:
bet = np.array(list(nx.betweenness_centrality(nx.Graph(mat_s)).values()))
bet = (bet-np.min(bet))/(np.max(bet)-np.min(bet))
bet_q = np.quantile(bet,[.2,.4,.6,.8])

In [ ]:
node_value = []
for i in bet:
  if i > bet_q[3]:
    node_value.append(25)
  elif i > bet_q[2]:
    node_value.append(20)
  elif i>bet_q[1]:
    node_value.append(15)
  elif i>bet_q[0]:
    node_value.append(10)
  else:
    node_value.append(5)

net = matPresentGraph(mat = mat,node_id = pers,node_type = node_type,node_value=node_value)
net.show("./pers_bet_netWork.html")
IPython.display.HTML('pers_bet_netWork.html')

./pers_bet_netWork.html


7淺綠色為群體間的broker（中介者）

Transitivity/Density/Distance/Diameter/Clustering

計算最大的subgraph 的 measure

In [ ]:
# 計算max subgraph
G = nx.Graph(mat_s)
G_sub = sorted(nx.connected_components(G), key=len, reverse=True)
G_max_sub = G.subgraph(G_sub[0])
# # 重新定義 mat
sub_mat = nx.adjacency_matrix(G_max_sub).todense()
node_idx = list(G_max_sub.nodes)
sub_pers = pers[node_idx]


畫出最大subgraph

In [ ]:
net = matPresentGraph(mat=sub_mat,node_id=sub_pers,directed=False)
net.show("./max_sub.html")
IPython.display.HTML('max_sub.html')

matrix is Symmetric
./max_sub.html


8由此圖可以看見和上述圖片差異相差不大，故推測會回覆某篇美食版貼文的使用者，也會回覆其他篇美食版貼文。

*計算transitivity（遞移性）* 

In [ ]:
nx.transitivity(nx.Graph(sub_mat))

0.004250495891187305

計算density 及 distance

In [ ]:
nx.density(nx.Graph(sub_mat))

0.00770941438102298

In [ ]:
nx.average_shortest_path_length(nx.Graph(sub_mat))

5.00449715838893



```
# 此內容會顯示為程式碼
```

計算diameter 直徑

In [ ]:
nx.diameter(nx.Graph(sub_mat))

10

計算clustering

In [ ]:
nx.average_clustering(nx.Graph(sub_mat))

0.0077048931714465965